In [3]:
import torch
import torch.nn as nn
import torchvision
import numpy as np
import  os
import pickle
import dataloadr
import vgg16
import pandas as pd

device = torch.device('cuda:1' if torch.cuda.is_available() else 'cpu')

Initializing Datasets and Dataloaders...
Files already downloaded and verified


In [4]:
model = vgg16.vgg16(in_channels=3,num_classes=10)
model.load_state_dict(torch.load('./model/vgg16.model',map_location='cpu'))

Generate model VGG16 


IncompatibleKeys(missing_keys=[], unexpected_keys=[])

In [5]:

class VggFeatureExtractor(nn.Module):
    def __init__(self, trained_model):
        super(VggFeatureExtractor,self).__init__()
        self.target_layer = nn.Sequential(*list(trained_model.children())[:-1])


    def forward(self, x):
        x = self.target_layer(x)
        return  x


def feature_extractor_v1(imag_root_dir,feature_save_path,name_save,save_container):
    with torch.no_grad():
        img_names = []
        dloader = dataloadr.get_dataloader(root_dir=imag_root_dir,batch_size=40)
        print('loade...')
        count = 0
        for batchimg,img_name in dloader:
                batchimg = batchimg.to('cpu')
                model.forward(batchimg)
                features = model.extract_features
                features = features.detach().numpy()
                features = features.astype(np.float16)
               
                save_container[count:count+features.shape[0],:] = features
                img_names.extend(img_name)
                count += features.shape[0]
                
                print(count)
                
        pickle.dump(img_names,open(name_save,'wb'))
        np.save(feature_save_path,save_container)

In [6]:
rest_save_container = np.zeros((665,512),dtype=np.float16)#665的意思是665涨图片在下面这个文件夹下          
feature_extractor_v1(imag_root_dir=os.path.abspath(os.path.join(os.getcwd(), "../VisualGenome/RestVisualGeneome")),
                     feature_save_path='../result/rest_feature.npy',
                     name_save = '../result/rest_names.pkl',
                     save_container=rest_save_container)

loade...
40
80
120
160
200
240
280
320
360
400
440
480
520
560
600
640
665


In [7]:

std_save_container = np.zeros((273,512),dtype=np.float16)#你的1000张图片在std1000这个文件夹下，不过暂时放了273张     
feature_extractor_v1(imag_root_dir=os.path.abspath(os.path.join(os.getcwd(), "../VisualGenome/std1000")),
                     feature_save_path='../result/std_feature.npy',
                     name_save = '../result/std_names.pkl',
                     save_container=std_save_container)

loade...
40
80
120
160
200
240
273


In [8]:
def feature_extractor_v2(imag_root_dir,feature_save_path,save_container):
    with torch.no_grad():
        extractor = VggFeatureExtractor(model)
        dloader = dataloadr.get_dataloader(root_dir=imag_root_dir,batch_size=10)
        print('loade...')
        for batchimg,img_name in dloader:
            batchimg = batchimg.to('cpu')
            features = extractor(batchimg)
            features = features.detach().numpy()
            print(img_name)
            break

# Compare

In [9]:
from numpy import linalg

In [10]:
std1000 = np.load('../result/std_feature.npy')
rest = np.load('../result/rest_feature.npy')
std_names = pickle.load(open('../result/std_names.pkl','rb'))
rest_names = pickle.load(open('../result/rest_names.pkl','rb'))

In [11]:
std_names = np.asarray(std_names)
rest_names = np.asarray(rest_names)

In [12]:
def calcu_simi():
    res_dict = {}
    for std_idx, std_item in enumerate(std1000):
        simi_vec = []
        for rest_idx,rest_item in enumerate(rest):
            simi = 1.0/(1.0+linalg.norm(std_item-rest_item))
            simi_vec.append(simi)
        top50 = np.argsort(np.asarray(simi_vec))[::-1][:51]
        top50_images = rest_names[top50]
        res_dict[std_names[std_idx]] = top50_images
    return res_dict

def write_into_excel(res_dict):  #写入excel
    pd_look = pd.DataFrame(res_dict)
    pd_look.to_excel('G://ImageRetrieval//TOP50\VggSimi//result//simi_50.xlsx', sheet_name='simi_50')

In [13]:
res_dict = calcu_simi()

In [14]:
res_dict

{'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\std1000\\1.jpg': array(['C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\839.jpg',
        'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\366.jpg',
        'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\654.jpg',
        'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\927.jpg',
        'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\921.jpg',
        'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\831.jpg',
        'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\627.jpg',
        'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\987.jpg',
        'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\953.jpg',
        'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\769.jpg',
        'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\758.jpg',


In [22]:
res_dict.values()

dict_values([array(['C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\366.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\846.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\987.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\627.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\624.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\432.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\419.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\935.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\731.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\685.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisualGeneome\\511.jpg',
       'C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\RestVisu

In [34]:
res_dict.keys(1)

TypeError: keys() takes no arguments (1 given)

In [30]:
for i in res_dict.keys():
    l = re.findall(r'\d+\.+jpg', i)
    print(l)

['1.jpg']
['100.jpg']
['101.jpg']
['102.jpg']
['103.jpg']
['104.jpg']
['105.jpg']
['106.jpg']
['107.jpg']
['108.jpg']
['109.jpg']
['110.jpg']
['111.jpg']
['112.jpg']
['113.jpg']
['114.jpg']
['115.jpg']
['116.jpg']
['117.jpg']
['118.jpg']
['119.jpg']
['120.jpg']
['121.jpg']
['122.jpg']
['123.jpg']
['124.jpg']
['125.jpg']
['126.jpg']
['127.jpg']
['128.jpg']
['129.jpg']
['130.jpg']
['131.jpg']
['132.jpg']
['133.jpg']
['134.jpg']
['135.jpg']
['136.jpg']
['137.jpg']
['138.jpg']
['139.jpg']
['140.jpg']
['141.jpg']
['142.jpg']
['143.jpg']
['144.jpg']
['145.jpg']
['146.jpg']
['147.jpg']
['148.jpg']
['149.jpg']
['150.jpg']
['151.jpg']
['152.jpg']
['153.jpg']
['154.jpg']
['155.jpg']
['156.jpg']
['157.jpg']
['158.jpg']
['159.jpg']
['160.jpg']
['161.jpg']
['162.jpg']
['163.jpg']
['164.jpg']
['165.jpg']
['166.jpg']
['167.jpg']
['168.jpg']
['169.jpg']
['170.jpg']
['171.jpg']
['172.jpg']
['173.jpg']
['174.jpg']
['175.jpg']
['176.jpg']
['177.jpg']
['178.jpg']
['179.jpg']
['180.jpg']
['181.jpg']
['182.

In [ ]:
'''import re
import shutil
fileDir = "C:/Users/js/Desktop\VggSimi/VisualGenome/std1000/"    #源图片文件夹路径
path = "G:/ImageRetrieval/ImageData/"   #移动到新的文件夹路径
for i in res_dict.keys():
    l = re.findall(r'\d+\.+jpg',i)
    #tarDir=os.path.join(path,str(l[0]))
  
    os.mkdir('G:/ImageRetrieval/ImageData/')
    tarDir = 'G:/ImageRetrieval/ImageData/l[0]/' 
    shutil.copy(fileDir+l[0],tarDir+l[0])
    print(l[0])
    
    break
'''
import re
import shutil
import os

fileDir = "C:/Users/js/Desktop\VggSimi/VisualGenome/std1000/"  # 源图片文件夹路径
file2Dir = 'C:/Users/js/Desktop/VggSimi/VisualGenome/RestVisualGeneome/'
path = "G:/ImageRetrieval/ImageData/"  # 移动到新的文件夹路径
l=[]
m=0
'''for i in res_dict.keys():
    l = re.findall(r'\d+\.+jpg', i)
    tarDir=os.path.join(path,str(l[0]).split(".")[0])
    if not os.path.exists(tarDir):
        os.mkdir(tarDir)
'''   
    #tarDir = tarDir+'/'+l[0]
    # tarDir = 'D:/Temp/2/l[0]/'''
for j in res_dict.values():
    j = str(j)
    p = re.findall(r'\d+\.+jpg',j)
    m = 0
    for i in res_dict.keys():
        l = re.findall(r'\d+\.+jpg', i)
        tarDir=os.path.join(path,str(l[0]).split(".")[0])
        if not os.path.exists(tarDir):
            os.mkdir(tarDir)
        
        shutil.copy(fileDir + l[0], tarDir)
        for k in p:
            shutil.copy(os.path.join(file2Dir, k), tarDir)
            print(k)
        '''break
    for m in range (0,51):
        print(p[m])
        #print(tarDir)
        shutil.copy(file2Dir + p[m], tarDir)
        m = m + 1
    '''
    
                 
    #shutil.copy(fileDir + l[0], tarDir)
    #print(tarDir)
    #print(l[0]+'-'+fileDir + l[0]+'-'+tarDir)
    




839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg
962.jpg
570.jpg
920.jpg
603.jpg
517.jpg
653.jpg
541.jpg
690.jpg
443.jpg
781.jpg
561.jpg
601.jpg
839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg
962.jpg
570.jpg
920.jpg
603.jpg
517.jpg
653.jpg
541.jpg
690.jpg
443.jpg
781.jpg
561.jpg
601.jpg
839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg


921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg
962.jpg
570.jpg
920.jpg
603.jpg
517.jpg
653.jpg
541.jpg
690.jpg
443.jpg
781.jpg
561.jpg
601.jpg
839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg
962.jpg
570.jpg
920.jpg
603.jpg
517.jpg
653.jpg
541.jpg
690.jpg
443.jpg
781.jpg
561.jpg
601.jpg
839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg


953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg
962.jpg
570.jpg
920.jpg
603.jpg
517.jpg
653.jpg
541.jpg
690.jpg
443.jpg
781.jpg
561.jpg
601.jpg
839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg
962.jpg
570.jpg
920.jpg
603.jpg
517.jpg
653.jpg
541.jpg
690.jpg
443.jpg
781.jpg
561.jpg
601.jpg
839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg


786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg
962.jpg
570.jpg
920.jpg
603.jpg
517.jpg
653.jpg
541.jpg
690.jpg
443.jpg
781.jpg
561.jpg
601.jpg
839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg
962.jpg
570.jpg
920.jpg
603.jpg
517.jpg
653.jpg
541.jpg
690.jpg
443.jpg
781.jpg
561.jpg
601.jpg
839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg


958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg
962.jpg
570.jpg
920.jpg
603.jpg
517.jpg
653.jpg
541.jpg
690.jpg
443.jpg
781.jpg
561.jpg
601.jpg
839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg
962.jpg
570.jpg
920.jpg
603.jpg
517.jpg
653.jpg
541.jpg
690.jpg
443.jpg
781.jpg
561.jpg
601.jpg
839.jpg
366.jpg
654.jpg
927.jpg
921.jpg
831.jpg
627.jpg
987.jpg
953.jpg
769.jpg
758.jpg
355.jpg
786.jpg
554.jpg
683.jpg
935.jpg
958.jpg
593.jpg
983.jpg
713.jpg
351.jpg
893.jpg
587.jpg
741.jpg
494.jpg
375.jpg
686.jpg
675.jpg
848.jpg
819.jpg
720.jpg
432.jpg
452.jpg
947.jpg
415.jpg
996.jpg
598.jpg
731.jpg
496.jpg


...

389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg
521.jpg
528.jpg
903.jpg
946.jpg
691.jpg
953.jpg
493.jpg
874.jpg
501.jpg
641.jpg
525.jpg
573.jpg
389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg
521.jpg
528.jpg
903.jpg
946.jpg
691.jpg
953.jpg
493.jpg
874.jpg
501.jpg
641.jpg
525.jpg
573.jpg
389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg


405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg
521.jpg
528.jpg
903.jpg
946.jpg
691.jpg
953.jpg
493.jpg
874.jpg
501.jpg
641.jpg
525.jpg
573.jpg
389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg
521.jpg
528.jpg
903.jpg
946.jpg
691.jpg
953.jpg
493.jpg
874.jpg
501.jpg
641.jpg
525.jpg
573.jpg
389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg


979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg
521.jpg
528.jpg
903.jpg
946.jpg
691.jpg
953.jpg
493.jpg
874.jpg
501.jpg
641.jpg
525.jpg
573.jpg
389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg
521.jpg
528.jpg
903.jpg
946.jpg
691.jpg
953.jpg
493.jpg
874.jpg
501.jpg
641.jpg
525.jpg
573.jpg
389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg


354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg
521.jpg
528.jpg
903.jpg
946.jpg
691.jpg
953.jpg
493.jpg
874.jpg
501.jpg
641.jpg
525.jpg
573.jpg
389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg
521.jpg
528.jpg
903.jpg
946.jpg
691.jpg
953.jpg
493.jpg
874.jpg
501.jpg
641.jpg
525.jpg
573.jpg
389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg


395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg
521.jpg
528.jpg
903.jpg
946.jpg
691.jpg
953.jpg
493.jpg
874.jpg
501.jpg
641.jpg
525.jpg
573.jpg
389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg
521.jpg
528.jpg
903.jpg
946.jpg
691.jpg
953.jpg
493.jpg
874.jpg
501.jpg
641.jpg
525.jpg
573.jpg
389.jpg
960.jpg
733.jpg
571.jpg
405.jpg
414.jpg
592.jpg
982.jpg
979.jpg
628.jpg
704.jpg
569.jpg
354.jpg
381.jpg
457.jpg
789.jpg
395.jpg
888.jpg
600.jpg
775.jpg
471.jpg
776.jpg
763.jpg
390.jpg
489.jpg
357.jpg
673.jpg
770.jpg
920.jpg
626.jpg
755.jpg
472.jpg
380.jpg
713.jpg
614.jpg
446.jpg
340.jpg
537.jpg
602.jpg


In [35]:
import re
import shutil
file2Dir = 'C:/Users/js/Desktop/VggSimi/VisualGenome/RestVisualGeneome/'
tarDir = 'G:/ImageRetrieval/ImageData/1'
x = []
x = res_dict.values()
x[1]
#for j in res_dict.values():
    #print(j)
    #j = str(j)
    #p = re.findall(r'\d+\.+jpg',j)
    #m==0
    #for m in range (0,51):
        #shutil.copy(file2Dir + p[m], tarDir)
        #print(p[m])
        #m = m + 1
        
    #break 

   
    

#p[1]



TypeError: 'dict_values' object does not support indexing

In [20]:
from glob import glob
import shutil
import os

In [21]:
rootPath = "C:\\Users\\js\\Desktop\\VggSimi\\VisualGenome\\std1000\\"
destPath = "G:\\ImageRetrieval\\ImageData\\"

In [23]:
for index, each in enumerate(glob(f"{rootPath}*jpg")):
    imageName = each.split("\\")[-1]
    imageNumber = imageName.split(".")[0]
    #print(index)
    #print(imageName, imageNumber)
    #print(each)
    #os.makedirs(f"{destPath}{imageNumber}")
    #shutil.copy(each, f"{destPath}{imageNumber}")
    

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272


In [28]:
for index, each in enumerate(res_dict.values().array[0]):
    imageName = each.split("\\")[-1]
    imageNumber = imageName.split(".")[0]
    print(imageNumber)

AttributeError: 'dict_values' object has no attribute 'array'